## A "Greedy" change approach

## How to generate itertool.product()-like iterators<br>How to count

In [8]:
# A trick for creating counting sequences without recursion
# Idea, add one to the first digit until the base is reached
# if the base is reached add one to the next digit and test
# and so on

base = 3
digits = 3
count = [0 for i in range(digits)]
while True:
    print(count)
    for i in range(digits):
        count[i] += 1
        if (count[i] < base):
            break
        count[i] = 0
    if (sum(count) == 0):
        break

[0, 0, 0]
[1, 0, 0]
[2, 0, 0]
[0, 1, 0]
[1, 1, 0]
[2, 1, 0]
[0, 2, 0]
[1, 2, 0]
[2, 2, 0]
[0, 0, 1]
[1, 0, 1]
[2, 0, 1]
[0, 1, 1]
[1, 1, 1]
[2, 1, 1]
[0, 2, 1]
[1, 2, 1]
[2, 2, 1]
[0, 0, 2]
[1, 0, 2]
[2, 0, 2]
[0, 1, 2]
[1, 1, 2]
[2, 1, 2]
[0, 2, 2]
[1, 2, 2]
[2, 2, 2]


## Another Approach

In [9]:
def exhaustiveChange(amount, denominations):
    bestN = 100
    count = [0 for i in range(len(denominations))]
    while True:
        for i, coinValue in enumerate(denominations):
            count[i] += 1
            if (count[i]*coinValue < 100):
                break
            count[i] = 0
        n = sum(count)
        if n == 0:
            break
        value = sum([count[i]*denominations[i] for i in range(len(denominations))])
        if (value == amount):
            if (n < bestN):
                solution = [count[i] for i in range(len(denominations))]
                bestN = n
    return solution

%time print(exhaustiveChange(40,[25,20,10,5,1]))

[0, 2, 0, 0, 0]
CPU times: user 578 ms, sys: 0 ns, total: 578 ms
Wall time: 577 ms


## Correct, but costly
* Our algorithm now gets the right answer for every value 1..100
* It must, because it considers every possible answer<br>(that’s the good thing about brute force)
* There is a downside though

In [10]:
%time print(exhaustiveChange(40, [25,10,5,1]))
%time print(exhaustiveChange(40, [25,20,10,5,1]))
%time print(exhaustiveChange(40, [13,11,7,5,3,1]))

[1, 1, 1, 0]
CPU times: user 125 ms, sys: 0 ns, total: 125 ms
Wall time: 123 ms
[0, 2, 0, 0, 0]
CPU times: user 547 ms, sys: 0 ns, total: 547 ms
Wall time: 544 ms
[0, 3, 1, 0, 0, 0]
CPU times: user 2min 5s, sys: 15.6 ms, total: 2min 5s
Wall time: 2min 7s


## Other tricks?

A Branch-and-bound algorithm

In [11]:
def branchAndBoundChange(amount, denominations):
    bestN = amount
    count = [0 for i in range(len(denominations))]
    while True:
        for i, coinValue in enumerate(denominations):
            count[i] += 1
            if (count[i]*coinValue < amount):             # Set upper bound to amount rather than 100
                break
            count[i] = 0
        n = sum(count)
        if n == 0:
            break
        if (n > bestN):                                   # don't compute the amount if there are too many coins
            continue
        value = sum([count[i]*denominations[i] for i in range(len(denominations))])
        if (value == amount):
            if (n < bestN):
                solution = [count[i] for i in range(len(denominations))]
                bestN = n
    return solution

%time print(branchAndBoundChange(42, [13,11,7,5,3,1]))

[1, 2, 1, 0, 0, 0]
CPU times: user 281 ms, sys: 0 ns, total: 281 ms
Wall time: 304 ms


## A Recursive Coin-Change Algorithm

In [12]:
def RecursiveChange(M, c):
    if (M == 0):
        return [0 for i in range(len(c))]
    smallestNumberOfCoins = M+1
    for i in range(len(c)):
        if (M >= c[i]):
            thisChange = RecursiveChange(M - c[i], c)
            thisChange[i] += 1
            if (sum(thisChange) < smallestNumberOfCoins):
                bestChange = thisChange
                smallestNumberOfCoins = sum(thisChange)
    return bestChange

%time print(RecursiveChange(42, [13,11,7,5,3,1]))

[3, 0, 0, 0, 1, 0]
CPU times: user 9min 21s, sys: 578 ms, total: 9min 21s
Wall time: 9min 29s


## Change via Dynamic Programming

In [24]:
def DPChange(M, c):
    change = [[0 for i in range(len(c))]]
    for m in range(1,M+1):
        bestNumCoins = m+1
        for i in range(len(c)):
            if (m >= c[i]):
                thisChange = [x for x in change[m - c[i]]]
                thisChange[i] += 1
                if (sum(thisChange) < bestNumCoins):
                    bestCombination = [v for v in thisChange]
                    bestNumCoins = sum(thisChange)
        change.append(bestCombination)
    return change[M]

%time print(DPChange(40, [1,3,5,7,11,13]))
%time print(DPChange(40, [1,3,5,7,11,13,17]))
%time print(DPChange(40, [1,3,5,7,11,13,17,19]))
%time print(DPChange(42, [13,11,7,5,3,1]))

[1, 0, 0, 0, 0, 3]
CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 531 µs
[1, 0, 1, 0, 0, 0, 2]
CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 860 µs
[2, 0, 0, 0, 0, 0, 0, 2]
CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 536 µs
[3, 0, 0, 0, 1, 0]
CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 178 µs


## A Hybrid Approach: Memoization

In [14]:
change = {}                                            # This is a cache for saving bestChange[M]

def MemoizedChange(M, c):
    global change
    if (M in change):                                   # Check the cache first
        return [v for v in change[M]]
    if (len(change) == 0):                              # Initialize cache
        change[0] = [0 for i in range(len(c))]
    smallestNumberOfCoins = M+1
    for i in range(len(c)):
        if (M >= c[i]):
            thisChange = MemoizedChange(M - c[i], c)
            thisChange[i] += 1
            if (sum(thisChange) < smallestNumberOfCoins):
                bestChange = [v for v in thisChange]
                smallestNumberOfCoins = sum(thisChange)
    change[M] = [v for v in bestChange]                 # Add new M to cache 
    return bestChange

%time print(MemoizedChange(99, [1,7,42]))

[1, 2, 2]
CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 1.62 ms
